In [1]:
import mph

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import peewee

from modules import comsol, utilites

import mph as _mph
import re as _re
import pandas as _pd 

In [2]:
client = mph.start()

In [200]:
model = client.load('models/Test1.mph')

In [194]:
client.clear()

In [195]:
class AbstractStudy:

    def __init__(self, model: _mph.Model):
        self.comsol_model = model
        self.study_name = self.__class__.__name__

    @property
    def model_parametrs(self):
        return self.comsol_model.parameters()

    @property
    def constants(self):
        rule = lambda key: ('K' == key[0]) or (key == 'light')
        return {
            key: value
            for key, value in model.parameters().items()
            if rule(key)
        } #yapf: disable

    @property
    def initial(self):
        # FIXME: 0 -> init_
        rule = lambda key: '0' in key
        return {
            key: value
            for key, value in model.parameters().items()
            if rule(key)
        } #yapf: disable

    @property
    def study_node(self):
        return self.comsol_model / 'studies' / f'{self.study_name}'

    @property
    def solution_node(self):
        return self.comsol_model / 'solutions' / f'{self.study_name}_Solution'

    @property
    def dataset_node(self):
        return self.comsol_model / 'datasets' / f'{self.study_name}_data'

    def set_parametrs(self, **kwargs):
        for key, value in kwargs.items():
            self.comsol_model.parameter(name=key, value=value)

    @staticmethod
    def _set_node_properties(node: mph.Node, **kwargs):
        for key, value in kwargs.items():
            node.property(key, value)

    def get_species(self) -> dict:
        model = self.comsol_model
        reaction_node = model / 'physics' / 'Reaction Engineering'
        reaction_node_children = [i.name() for i in reaction_node.children()]

        species = _re.findall(
            string='\n'.join(reaction_node_children),
            pattern='Species: (.*)',
        )
        return {specie: f'reaction.c_{specie}' for specie in species}

    def _temporal_eval(
        self,
        outer_number,
        functions={},
        eval_species=False,
    ) -> _pd.DataFrame:

        model = self.comsol_model
        full_dict = {'time': 't'}

        if isinstance(functions, dict):
            full_dict.update(functions)
        elif isinstance(functions, list):
            full_dict.update({key: key for key in functions})

        if eval_species:
            full_dict.update(self.get_species())

        columns = list(full_dict)
        expressions = [full_dict[key] for key in columns]

        row_data = model.evaluate(
            expressions,
            dataset=self.dataset_node.name(),
            outer=outer_number,
        )
        return _pd.DataFrame(row_data, columns=columns)

    def _solve_one(self):
        self.comsol_model.solve(study=self.study_node.name())


class Generator(AbstractStudy):

    def temporal_eval(
        self,
        functions={},
        eval_species=False,
    ) -> _pd.DataFrame:

        return self._temporal_eval(
            outer_number=1,
            functions=functions,
            eval_species=eval_species,
        )

    def solve(self):
        self._solve_one()


class Sweeper(AbstractStudy):

    @property
    def light_diap(self):
        rule = lambda key: 'light' in key
        result = {
            key: value
            for key,value in model.parameters().items()
            if rule(key)
        } #yapf: disable
        result.pop('light')
        return result

    def temporal_eval(
        self,
        functions={},
        light_list: list = [],
        eval_species=False,
    ) -> _pd.DataFrame:

        if light_list == []:
            light_list = self.comsol_model.outer(self.dataset_node.name())[1]

        dfs = []
        for i in range(len(light_list)):
            df = self._temporal_eval(
                outer_number=i + 1,
                functions=functions,
                eval_species=eval_species,
            )
            df['light'] = light_list[i]
            dfs.append(df)
        result = pd.concat(dfs)
        return result


class Estimator(AbstractStudy):

    @property
    def estimation_node(self):
        return self.comsol_model / 'physics' / 'Reaction Engineering' / 'Estimation'

    @property
    def experiments(self):
        return self.estimation_node.children()

    @property
    def tables(self):
        tables = self.comsol_model / 'tables'
        experiment_tables = [
            node for node in tables.children() if 'Experiment' in node.name()
        ]
        return experiment_tables

    def create_experiment(
        self,
        data,
        experiment_i,
        usable_species: dict = ['Q', 'DH', 'QHH'],
    ):
        # TODO: path -> python)

        path = r'D:\WORKS\COMSOL_polymers\Batch\generator_out_short.csv'
        experiment_name = f'exp{experiment_i}'

        # create experiment
        self.estimation_node.java.create(experiment_name, "Experiment", -1)
        experiment = self.experiments[-1]

        # create table
        table_tag = f"tbl_compreactionest1{experiment_name}"
        table = (model / 'tables').java.create(table_tag, "Table")
        table.label(f"Experiment {experiment_i} Table")
        table.setTableData(data)
        table.active(False)

        # set up parametrs
        # FIXME: columns from data
        data_columns = ['Time', 'Q','QHD', 'QHH']

        usable_columns = [
            1 if key in usable_species + ['Time'] else 0 for key in data_columns
        ]
        variables = [self.get_species().get(key, 't') for key in data_columns]
        Estimator._set_node_properties(
            node=experiment,
            fileName=path,
            dataColumn=data_columns,
            use=usable_columns,
            modelVariable=variables,
        )

    def clear_experiments(self):
        experiments, tables = self.experiments, self.tables
        for table in tables:
            table.remove()
        for experiment in experiments:
            experiment.remove()

    def solve(self):
        self.estimation_node.toggle('on')
        try:
            self._solve_one()
        finally:
            self.estimation_node.toggle('off')

In [201]:
gen=Generator(model)
swe=Sweeper(model)
est =Estimator(model)

In [158]:
mph.tree(est.estimation_node)

Estimation
└─ Experiment 1


In [197]:
a="""
0,0.9999600023998281,3.1991809344282185E-20,3.199179656856224E-20
2.0E-5,0.5050493401675912,0.24554633247812718,0.24358797825235726
4.0E-5,0.4024130448705575,0.2992622404213495,0.2949331949045941
6.000000000000001E-5,0.36386541970220765,0.3201900722138979,0.3136659994089529
8.0E-5,0.3464142293906715,0.3302323270170087,0.32170420488527623
1.0E-4,0.3377853182006684,0.33562983218236137,0.32532258174847917
1.2000000000000002E-4,0.3332956055191216,0.33874938182612596,0.32693866426754253
1.4000000000000001E-4,0.3308837119190126,0.3406292409004375,0.3276292010579907
1.6E-4,0.3295651566308297,0.3417765943006531,0.3279037114510749
1.8E-4,0.3288409200835633,0.3424698074723245,0.32800294028021965
2.0E-4,0.3284450049193148,0.342879258439495,0.32803497831193684
""".split('\n')[1:-1]

In [198]:
b =[[float(ii) for ii in i.split(",")] for i in a]

In [202]:
est.experiments

[]

In [169]:
est.clear_experiments()

In [203]:
est.create_experiment(
    data=b,
    experiment_i=1,
)
est.experiments

[Node('physics/Reaction Engineering/Estimation/Experiment 1')]

In [204]:
est.solve()

In [50]:
# experiment_i = 1
# experiment_name = f'exp{experiment_i}'
# data = (
#     (0, 0.9996002398321241),
#     (7.107141824976009E-12, 0.9995931384723676),
#     (1.4214283649952018E-11, 0.9995860372135092),
#     (2.8428567299904037E-11, 0.9995718349312134),
# )

# # create experiment
# estimator = model / 'physics' / 'Reaction Engineering' / 'Estimation'
# estimator.java.create(experiment_name, "Experiment", -1)

# # create table
# table_tag = f"tbl_compreactionest1{experiment_name}"
# table_label = f"Experiment {experiment_i} Table"
# table = (model / 'tables').java.create(table_tag, "Table")
# table.label(table_label)
# table.setTableData(data)
# table.active(False)

# set up settings
# path = 'D:\\WORKS\\COMSOL_polymers\\Batch\\generator_out_short.csv'
# columns = []
# usable_columns = [1,1]
# variables = []
# dict(
#     fileName=path,
#     dataColumn=columns,
#     use=usable_columns,
#     modelVariable=variables,
# )

# Sweep

In [2]:
client = mph.start()
model = client.load('System_batch.mph')

In [3]:
variative_params = combinations_dict({
    'Ks': np.linspace(0.1, 5.1, 11).round(5),
    'Kc': np.linspace(0.1, 2.1, 11).round(5),
})

In [4]:
model_parametrs(model, {
    'light_start': '0',
    'light_end': '5e-4',
})
model_parametrs(model)

{'Ke': '1000000000',
 'KH': '1000000000',
 'Kr': '1000000000',
 'Kdisp': '1000000000',
 'KqH': '2000',
 'Ks': '2',
 'Kd': '0.05',
 'Kc': '1',
 'Kp': '0.001',
 'KrD': '1000000000',
 'Kph': '1E-05',
 'light': '0.0001',
 'light_start': '0',
 'light_end': '5e-4',
 'light_step': '1e-5'}

In [5]:
db.connect()
sweep(
    model=model,
    name='sweep',
    desc='',
    variable_params=variative_params[:3],
)
db.close()

Saving... : 100%|██████████| 3/3 [04:11<00:00, 83.92s/it]


True

# Plots

In [3]:
import plotly.express as px

In [4]:
rule = {'Kc': (0, 0.30000)}
diap = ['Kc', 'light']
datas, dfs = get_solves(rule)
result = collect_dfs(datas, dfs, diap)


In [5]:
fig = px.line(
    result,
    x="Time",
    y="Q",
    animation_frame='light',
    color='Kc',
    range_y=[0, 1],
)
fig.update_layout(
    height=500,
    margin={
        'r': 0, 'l': 0, 't': 0, 'b': 0
    },
    legend=dict(x=-0.1, y=1, xanchor="left"),
)